# Overview
This notebook...
1. takes in the latitudes and longitudes from the raw_data folder
2. interpolates their intensity across the world into shapefiles
3. generates an app that let's users explore the maps 

In [1]:
import geopandas as gpd
import pandas as pd
import plotly.express as px

fallout_data = pd.read_csv("./raw_data/fallout_data_becquerel.csv")
fallout_point_gdf = gpd.GeoDataFrame(fallout_data, geometry=gpd.points_from_xy(fallout_data["LONG"], fallout_data["LAT"]))
fallout_col = "CASTLE TOTAL Bq/m2"


In [2]:
import numpy as np
from matplotlib import pyplot as plt
from shapely.geometry import Polygon, Point, MultiPoint
import geopy.distance
from statistics import NormalDist
from math import sin, cos, sqrt, atan2, radians

idx = ~fallout_data[fallout_col].isnull()

def inverse_distance_weighting(fallout_lats,fallout_longs,fallouts,long,lat,
                              standard_distance=250,
                               k_nearest = 4
#                               data_col = "CASTLE TOTAL"
                             ):
#     Assume longitude and latitude are numpy arrays in radians
    # approximate radius of earth in km
    R = 6373.0
    
    dlons = fallout_longs - long
    dlats = fallout_lats - lat
    
    a = np.sin(dlats / 2)**2 + np.cos(fallout_lats) * np.cos(lat) * np.sin(dlons / 2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))

    distances = R * c
    idx_nearest = np.argsort(distances)
    fallouts = np.array(fallouts)
    weights = 1/distances
#     weights = (1/distances)**1.5
#     weights = (1/distances)**2    
    fallout_weighted = np.sum(weights[idx_nearest[0:k_nearest]]*fallouts[idx_nearest[0:k_nearest]]/np.sum(weights[idx_nearest[0:k_nearest]]))
    return fallout_weighted

# Generate a regular grid with 60° longitude and 30° latitude steps:
# grid_lon = np.linspace(0.5, 359.5, 360)
# grid_lat = np.linspace(-89.5, 89.5, 180)
# grid_lon = np.linspace(1.0, 359, 180)
# grid_lat = np.linspace(-89, 89, 90)
# grid_lon = np.linspace(-179, 179, 180)
grid_lon = np.linspace(0.5, 359.5, 360)
grid_lat = np.linspace(-89.75, 89.75, 360)

fallouts = fallout_data.loc[idx,fallout_col].to_list()
fallout_lats_radians = np.deg2rad(fallout_data.loc[idx,"LAT"].to_numpy())
fallout_longs_radians = np.deg2rad(fallout_data.loc[idx,"LONG"].to_numpy())

polygons = []
points = []
data = []
lat_width = (grid_lat[1]-grid_lat[0])/2
long_width = (grid_lon[1]-grid_lon[0])/2
for (long,long_ind) in zip(grid_lon,range(len(grid_lon))):
    for (lat,lat_ind) in zip(grid_lat,range(len(grid_lat))):

#         fallout = gaussian_weighted_average(fallout_lats,fallout_longs,fallouts,long,lat)
        fallout = inverse_distance_weighting(fallout_lats_radians,fallout_longs_radians,
                                                    fallouts,radians(long),radians(lat))
        if not(np.isnan(fallout)):
            points.append(Point((long,lat)))
            data.append(fallout) 
            polygons.append(Polygon([(long-long_width,lat-lat_width), 
                         (long+long_width, lat-lat_width), 
                         (long+long_width, lat+lat_width), 
                         (long-long_width, lat+lat_width),
#                                  (x-x_width,y+y_width),
                        ]))
        else:
            print(long,lat)



In [3]:
# Following cutoffs for raw units
# fallout_intensity_bins = [[0,1000],
#                          [1000,2000],
#                          [2000,5000],
#                          [5000,10000],
#                          [10000,20000],
#                          [20000,50000],
#                          [50000,100000],
#                           [100000,200000],
#                           [200000,1000000000000]]

# fallout_cutoffs = [1000,2000,5000,10000,20000,50000,100000,200000,1000000000000]
# Following cutoffs for Becquerel units
polygon_gdf = gpd.GeoDataFrame(geometry = polygons)
polygon_gdf["fallout"] = data

# fallout_intensity_bins = [[0,100],
#                          [100,200],
#                          [200,500],
#                          [500,1000],
#                          [1000,2000],
#                          [2000,5000],
#                          [5000,10000],
#                           [10000,20000],
#                           [20000,1000000000000]]

# fallout_cutoffs = [100,200,500,1000,2000,5000,10000,20000,100000000000]

fallout_intensity_bins = [[0,100],
                         [100,200],
                         [200,400],
                         [400,800],
                         [800,1600],
                         [1600,3200],
                         [3200,6400],
                          [6400,12800],
                          [12800,25600],
                         [25600,10000000000000000]]


fallout_cutoffs = [100,200,400,800,1600,3200,6400,12800,25600,100000000000]


regions_polygons = []
min_fallout = []
for fallout_bin in fallout_intensity_bins:
    polygons_binned = polygon_gdf.loc[(polygon_gdf["fallout"]>=fallout_bin[0])&(polygon_gdf["fallout"]<fallout_bin[1]),"geometry"]
#     points_too_little = points_gdf.loc[points_gdf["fallout_kriging"]<fallout_cutoffs[cutoff_idx],"geometry"]
#     print(points_big_enough)
    if len(polygons_binned)>0:
        min_fallout.append(fallout_bin[0])
        regions_polygons.append(polygons_binned.unary_union)

In [106]:
import plotly.graph_objs as go
import matplotlib
import json
import shapely
# fallout_gdf["geometry_geojson"] = [json.dumps(shapely.geometry.mapping(pgon)) for pgon in fallout_gdf["geometry"]]
fallout_gdf = gpd.GeoDataFrame(geometry = regions_polygons, crs = 'epsg:4326')
fallout_gdf["Fallout Bq/m^2"] = [str(f) for f in min_fallout]
fallout_gdf = fallout_gdf.iloc[2:]

# cmap_str = 'YlOrRd'
cmap_str = 'inferno'
# cmap_str = 'hot'

# mapbox_style='carto-darkmatter'
# mapbox_style='carto-positron'
# mapbox_style='stamen- terrain'
# mapbox_style='stamen-toner'
mapbox_style='open-street-map'
#     color_discrete_sequence=px.colors.sequential.YlOrRd
#     color_discrete_sequence=px.colors.sequential.Blackbody
#     color_discrete_sequence=px.colors.sequential.Electric
#     color_discrete_sequence=px.colors.sequential.Hot
#     color_discrete_sequence=px.colors.sequential.Agsunset



cmap = matplotlib.cm.get_cmap(cmap_str)
# colors = [cmap(val) for val in np.linspace(0,1,len(fallout_gdf))]
colors = [matplotlib.colors.to_rgb(cmap(val)) for val in np.linspace(0.0,0.9,len(fallout_gdf))]
colors = ["rgb("+str(255*c[0])+","+str(255*c[1])+","+str(255*c[2])+")" for c in colors]


fig = px.choropleth_mapbox(
    fallout_gdf,
    geojson=fallout_gdf.geometry,
    locations=fallout_gdf.index,
    color=fallout_gdf["Fallout Bq/m^2"],
    mapbox_style=mapbox_style,
    color_discrete_sequence=colors,
    zoom=1,
    center={'lat': 10, 'lon': 165},
    opacity=0.4,
    hover_data = []
#     hoverinfo = 'skip'
)

# fallout_gdf["geometry_geojson"] = [json.dumps(shapely.geometry.mapping(pgon)) for pgon in fallout_gdf["geometry"]]
# fig = go.Figure(go.Choroplethmapbox(
#     fallout_gdf,
#     geojson=fallout_gdf["geometry_geojson"],
#     geojson = fallout_gdf.to_json(),
#     locations=fallout_gdf.index,
#     z=fallout_gdf["Fallout Bq/m^2"],
#     mapbox_style='carto-darkmatter',
#     color_discrete_sequence=px.colors.sequential.YlOrRd,
#     zoom=1,
#     center={'lat': 10, 'lon': 165},
#     opacity=0.4,
#     hover_info = None
#     hoverinfo = 'skip'
# ))

fig = fig.update_traces(
    marker_line_width=0,
#     opacity=0.4
)

fig.update_geos(projection_type="orthographic")

fig.update_layout(
    title_text='Castle Series Cumulative Fallout',
    geo=dict(
        showframe=False,
    ),
)
idx = ~fallout_data[fallout_col].isnull()


fallout_data["hover_text"] = [row["City"] + ": " + str(row[fallout_col]) for _,row in fallout_data.iterrows()]

fig.add_trace(go.Scattermapbox(lat = fallout_data.loc[idx,"LAT"].to_numpy(),
                               lon = fallout_data.loc[idx,"LONG"].to_numpy(),
                               marker=go.scattermapbox.Marker(size=40*fallout_data.loc[idx,fallout_col]/np.max(fallout_data.loc[idx,fallout_col]),
                                                              color='rgb(160,160,160)',
                                                              opacity=0.7
                                                             ),
                               hovertext = fallout_data.loc[idx,"hover_text"],
                               name = "Measured Fallout"
#                      size = fallout_data.loc[idx,"CASTLE TOTAL"],
#                      hovertemplate='City: $%{y:.2f}'+'<br>Week: %{x}')
#                      hover_text = fallout_data.loc[idx,"hover_text"],
#                      hover_name = "City",
#                      hover_data = ["CASTLE TOTAL"],
#                     projection = "natural earth")
                                      ))


fig.show()
fig.write_html("Castle_fallout_"+cmap_str+"_on_"+str(mapbox_style)+".html")


In [81]:
fallout_data.iloc[15,:]

City                                       Beirut
LAT                                      34.00071
LONG                                     35.48292
Hemisphere                               Atlantic
CASTLE TOTAL dpm/ft2                          NaN
CASTLE TOTAL Bq/m2                            NaN
Unnamed: 6                                    NaN
Unnamed: 7                                    NaN
Unnamed: 8                                    NaN
Unnamed: 9                                    NaN
Unnamed: 10                                   NaN
Unnamed: 11                                   NaN
Unnamed: 12                                   NaN
geometry                POINT (35.48292 34.00071)
hover_text                            Beirut: nan
Name: 15, dtype: object

In [107]:
fallouts = fallout_data.loc[:,fallout_col].to_list()
fallout_lats_radians = np.deg2rad(fallout_data.loc[:,"LAT"].to_numpy())
fallout_longs_radians = np.deg2rad(fallout_data.loc[:,"LONG"].to_numpy())

idx_max = np.nanargmax(fallouts)
long = fallout_longs_radians[idx_max]
lat = fallout_lats_radians[idx_max]
R = 6373.0

dlons = fallout_longs_radians - long
dlats = fallout_lats_radians - lat

a = np.sin(dlats / 2)**2 + np.cos(fallout_lats_radians) * np.cos(lat) * np.sin(dlons / 2)**2
c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))

distances = R * c

fallout_data["Distance from maximum (km)"] = distances
fallout_data["Fallout (Bq/m^2)"] = fallouts

fig = px.scatter(fallout_data,x="Distance from maximum (km)",
                 y="Fallout (Bq/m^2)",
                 color = "LAT",
                 hover_data = ["City"])
fig.show()
fig.write_html("Distance_scatterplot.html")


In [76]:
print(distances,fallouts)


[10370.23665498  9541.16204797 12351.91967665  5486.91220482
  2822.40461652  5115.80026116  5683.3616204   5637.79107868
  3778.99158467  4302.0833007   2038.46625792  4591.54214341
  2725.17076253  6666.70228416  7061.24199345     0.
  1579.66812108  3968.03850105  5326.08015522  5182.14194531
  3407.53558404  3906.38839103  6836.45508741  7856.67889108
  7449.30056698  8319.9372526   8449.33156234  8939.73368565
  8719.98621501  8588.12481088  8123.20816754  8597.71228168
 10367.14927691 10511.15208895  9777.61999401 11878.37872829
 12428.19287345 12978.97605974 12153.63153189 13100.78409975
 13441.50902832 13575.00995031 14148.53543114 16569.58930462
 12279.00453369 13202.37518296 13786.51958387  9575.6976716
  9949.90127123 15529.4449925  13596.61627843 13707.73637393
 13929.03735279 15087.51798184  8893.92742601  9004.17397217
  9330.30139846  9707.14034194 10620.17166897 11232.22782064
 11693.45022358 11948.5898659  10875.53149756 11595.10917072
 11807.31884343  9832.6078171  10

# Archived code for map